# Context BoW

### NLP Technologies
### Miguel Soto

In [7]:
import sys
sys.path.append('/Users/mash/Documents/Git/ciencias_de_la_computacion/Doctorado/Scripts')

In [ ]:
import text_preprocessing as tp
import pandas as pd, numpy as np
from collections import defaultdict
from typing import Union, List

In [12]:
def normalize_text(text: str) -> List[str]:
    """Normaliza y tokeniza el texto."""
    return text.lower().split()

def get_separate_contextual_bow(text: Union[str, List[str], pd.DataFrame], window_size: int = 2) -> dict:
    """Genera las bolsas de palabras contextuales separando contexto izquierdo y derecho."""
    # Preparar los datos de entrada
    if isinstance(text, pd.DataFrame):
        documents = [row for row in text.iloc[:,0].apply(normalize_text)]
    elif isinstance(text, list):
        documents = [normalize_text(doc) for doc in text]
    else: # asumimos que es un string
        documents = [normalize_text(text)]
    
    # Diccionario para almacenar contextos izquierdo, derecho y combinado
    bow_contextual = defaultdict(lambda: {"left": defaultdict(int), "right": defaultdict(int), "combined": defaultdict(int)})
    
    # Procesar cada documento
    for doc in documents:
        for index, word in enumerate(doc):
            # Contexto izquierdo
            left_context = doc[max(0, index - window_size):index]
            for context_word in left_context:
                bow_contextual[word]["left"][context_word] += 1
                bow_contextual[word]["combined"][context_word] += 1
            
            # Contexto derecho
            right_context = doc[index+1:min(len(doc), index + window_size + 1)]
            for context_word in right_context:
                bow_contextual[word]["right"][context_word] += 1
                bow_contextual[word]["combined"][context_word] += 1
    
    return bow_contextual


In [5]:
# Reading the file
filename = '../data/e990519_mod.htm'
text_file = open(filename, encoding='utf-8')
text = text_file.read()
text_file.close()

In [15]:
# Cleaning the text
prep_es = tp.Preprocessing(language='spanish')
cleaned_text = prep_es.main_preprocess(text, tweet=True)

In [39]:
tokens = cleaned_text.split()
print(f'Raw tokens: {len(tokens)}')

Raw tokens: 108372


In [16]:
# Trying the function with the cleaned text
separate_bow_contextual = get_separate_contextual_bow(cleaned_text, window_size=2)
for word, contexts in separate_bow_contextual.items():
    print(f"Palabra: {word}")
    print(f"\tContexto Izquierdo: {contexts['left']}")
    print(f"\tContexto Derecho: {contexts['right']}")
    print(f"\tContexto Combinado: {contexts['combined']}")

Palabra: mod
	Contexto Izquierdo: defaultdict(<class 'int'>, {'ciudadanos': 1, 'nacionales': 1})
	Contexto Derecho: defaultdict(<class 'int'>, {'htm': 2, 'excelsior': 2})
	Contexto Combinado: defaultdict(<class 'int'>, {'htm': 2, 'excelsior': 2, 'ciudadanos': 1, 'nacionales': 1})
Palabra: htm
	Contexto Izquierdo: defaultdict(<class 'int'>, {'mod': 2, 'nacionales': 1})
	Contexto Derecho: defaultdict(<class 'int'>, {'excelsior': 2, 'editorial': 2})
	Contexto Combinado: defaultdict(<class 'int'>, {'mod': 2, 'excelsior': 2, 'editorial': 2, 'nacionales': 1})
Palabra: excelsior
	Contexto Izquierdo: defaultdict(<class 'int'>, {'mod': 2, 'htm': 2, 'nota': 130, 'siguiente': 130, 'traslosheros': 2, 'editorial': 2, 'primera': 2, 'plana': 2, 'os': 2, 'financiera': 2, 'articulista': 2, 'de': 8, 'foro': 8, 'alar': 2, 'que': 2, 'tel': 2})
	Contexto Derecho: defaultdict(<class 'int'>, {'editorial': 30, 'miercoles': 68, 'primera': 24, 'plana': 24, 'financiera': 28, 'foro': 10, 'que': 2, 'exige': 2, 'pu

In [21]:
def vectorize_bow(bow_dict):
    """Vectoriza la bolsa de palabras contextuales y retorna un vocabulario y los vectores."""
    vocab = sorted(set(word for context in bow_dict.values() for word in context['combined']))
    vocab_index = {word: i for i, word in enumerate(vocab)}
    
    vectors = {}
    for word, contexts in bow_dict.items():
        vector = np.zeros(len(vocab))
        for context_word, count in contexts['combined'].items():
            if context_word in vocab_index:
                vector[vocab_index[context_word]] = count
        vectors[word] = vector
    return vocab, vectors

def normalize_vectors(vectors):
    """Normaliza los vectores."""
    for word, vector in vectors.items():
        norm = np.linalg.norm(vector)
        if norm > 0:
            vectors[word] = vector / norm
    return vectors

def cosine_similarity(vector_a, vector_b):
    """Calcula la similitud coseno entre dos vectores."""
    return np.dot(vector_a, vector_b) / (np.linalg.norm(vector_a) * np.linalg.norm(vector_b))

In [41]:

# Utilizando el código anterior para obtener las bolsas de palabras contextuales
vocab, vectors = vectorize_bow(separate_bow_contextual)
vectors = normalize_vectors(vectors)

In [40]:
print(f"vocabulario: {len(vocab)}")
print(f"Tamaño de un vector (de): {len(vectors['de'])}")

vocabulario: 8765
Tamaño de un vector (de): 8765


In [27]:
vectors

{'mod': array([0., 0., 0., ..., 0., 0., 0.]),
 'htm': array([0., 0., 0., ..., 0., 0., 0.]),
 'excelsior': array([0., 0., 0., ..., 0., 0., 0.]),
 'editorial': array([0., 0., 0., ..., 0., 0., 0.]),
 'miercoles': array([0.0086724, 0.       , 0.       , ..., 0.       , 0.       ,
        0.       ]),
 'de': array([0.14563707, 0.00118887, 0.        , ..., 0.        , 0.        ,
        0.        ]),
 'mayo': array([0.00526871, 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]),
 'epigrama': array([0., 0., 0., ..., 0., 0., 0.]),
 'jorge': array([0., 0., 0., ..., 0., 0., 0.]),
 'mansilla': array([0., 0., 0., ..., 0., 0., 0.]),
 'torres': array([0., 0., 0., ..., 0., 0., 0.]),
 'con': array([0.13802089, 0.        , 0.0053085 , ..., 0.        , 0.        ,
        0.        ]),
 'honores': array([0., 0., 0., ..., 0., 0., 0.]),
 'militares': array([0.17149859, 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]),
 'enterraron': array([0., 0., 0., ..., 

In [30]:
# Ejemplo de cálculo de similitud coseno entre dos palabras
word_a = 'de'
word_b = 'a'
similarity = cosine_similarity(vectors[word_a], vectors[word_b])
print(f"Similitud coseno entre '{word_a}' y '{word_b}': {similarity}")

Similitud coseno entre 'de' y 'a': 0.9169576419273844


In [32]:
# Ejemplo de cálculo de similitud coseno entre dos palabras
word_a = 'bandera'
word_b = 'pago'
similarity = cosine_similarity(vectors[word_a], vectors[word_b])
print(f"Similitud coseno entre '{word_a}' y '{word_b}': {similarity}")

Similitud coseno entre 'bandera' y 'pago': 0.15811388300841897


In [42]:
# Obtener las similitudes de todas las palabras
def get_all_cosine_similarities(word, vocabulary, vectors):
    """Obtiene las similitudes coseno de una palabra con todas las demás."""
    similarity_dict = {}
    for word_b in vocabulary:
        similarity_dict[word_b] = cosine_similarity(vectors[word], vectors[word_b])
    
    # Ordenarlas de mayor a menor similitud
    similarity_dict = dict(sorted(similarity_dict.items(), key=lambda x: x[1], reverse=True))
    return similarity_dict

In [48]:
# Similitud para una palabra (bandera)
bandera = get_all_cosine_similarities('bandera', vocab, vectors)
for word, similarity in bandera.items():
    print(f"{word}: {similarity}")

bandera: 1.0
contienda: 0.6648376737370495
misma: 0.6575959492214292
zona: 0.6531972647421808
creacion: 0.6527533657682199
especializacion: 0.6454972243679029
inactividad: 0.6454972243679029
sida: 0.6454972243679029
sucesoria: 0.6454972243679029
organizacion: 0.6391374907061421
estructura: 0.639009650422694
coyuntura: 0.6390096504226939
eleccion: 0.636396103067893
manufactura: 0.632455532033676
ampliacion: 0.6324555320336759
ribera: 0.6324555320336759
silicon: 0.6324555320336759
sre: 0.6324555320336759
vecina: 0.6324555320336759
demanda: 0.6296776178641135
capital: 0.6291982286679645
fecha: 0.619750683009635
sede: 0.6165812304904388
mexicana: 0.6094036879722642
clausula: 0.6
ejecucion: 0.6
reunion: 0.5978331360829092
cupula: 0.5976143046671969
region: 0.5938574464184706
telefonica: 0.59336610396393
segunda: 0.5929270612815711
ocde: 0.5924884902348261
fiebre: 0.5916079783099616
publicacion: 0.5916079783099616
entidad: 0.5855400437691199
poblacion: 0.5849616182167253
parlamentaria: 0.580

In [49]:
# Obtener las similitudes de todas las palabras y guardarlas en un diccionario
similarities_dict = {}
for word in vocab:
    similarities_dict[word] = get_all_cosine_similarities(word, vocab, vectors)

In [51]:
# Save similarities_dict into a txt
with open('similarities_dict.txt', 'w') as file:
    file.write(str(similarities_dict))

In [ ]:
# import pandas as pd
# from collections import defaultdict
# from typing import Union, List

# def normalize_text(text: str) -> List[str]:
#     """
#     Normaliza y tokeniza el texto.
    
#     Parámetros:
#     - text (str): Texto a normalizar y tokenizar.
    
#     Retorna:
#     - List[str]: Lista de tokens normalizados (palabras).
#     """
#     # Convertir todo el texto a minúsculas y dividir por espacios para obtener tokens individuales
#     return text.lower().split()

# def get_separate_contextual_bow(text: Union[str, List[str], pd.DataFrame], window_size: int = 2) -> dict:
#     """
#     Genera bolsas de palabras contextuales, separando los contextos izquierdo y derecho para cada palabra.
    
#     Parámetros:
#     - text (Union[str, List[str], pd.DataFrame]): Texto de entrada que puede ser un solo string, 
#       una lista de strings, o un DataFrame de pandas.
#     - window_size (int): Tamaño de la ventana de contexto para cada lado de la palabra.
    
#     Retorna:
#     - dict: Un diccionario que mapea cada palabra a otro diccionario con las bolsas de palabras 'left', 'right', y 'combined'.
#     """
#     # Preparar los datos de entrada dependiendo del tipo de objeto que se recibe (DataFrame, lista o string)
#     if isinstance(text, pd.DataFrame):
#         # Asume que los datos de texto están en la primera columna y los normaliza
#         documents = [row for row in text.iloc[:,0].apply(normalize_text)]
#     elif isinstance(text, list):
#         # Normaliza cada documento en la lista
#         documents = [normalize_text(doc) for doc in text]
#     else:  # asumimos que es un string
#         documents = [normalize_text(text)]
    
#     # Diccionario para almacenar contextos izquierdo, derecho y combinado para cada palabra
#     bow_contextual = defaultdict(lambda: {"left": defaultdict(int), "right": defaultdict(int), "combined": defaultdict(int)})
    
#     # Procesar cada documento para construir las bolsas de palabras contextuales
#     for doc in documents:
#         for index, word in enumerate(doc):
#             # Determinar los índices para el contexto izquierdo y derecho
#             left_context = doc[max(0, index - window_size):index]
#             right_context = doc[index+1:min(len(doc), index + window_size + 1)]
            
#             # Contar las ocurrencias de cada palabra en el contexto izquierdo y derecho
#             for context_word in left_context:
#                 bow_contextual[word]["left"][context_word] += 1
#                 bow_contextual[word]["combined"][context_word] += 1
                
#             for context_word in right_context:
#                 bow_contextual[word]["right"][context_word] += 1
#                 bow_contextual[word]["combined"][context_word] += 1
    
#     return bow_contextual

# # Ejemplo de uso
# text_example = "El rápido zorro marrón salta sobre el perro perezoso. El perro no se inmuta."
# separate_bow_contextual = get_separate_contextual_bow(text_example, window_size=2)
# for word, contexts in separate_bow_contextual.items():
#     print(f"Palabra: {word}")
#     print(f"\tContexto Izquierdo: {contexts['left']}")
#     print(f"\tContexto Derecho: {contexts['right']}")
#     print(f"\tContexto Combinado: {contexts['combined']}")
